In [1]:
import altair as alt
from altair import datum
import ipywidgets as widgets
from ipywidgets import interact, interact_manual
from IPython.display import HTML, Markdown as md

from src.data.read_dataset import get_processed_dataset
from src.visualization import visualize as viz

regioni_df = get_processed_dataset('dpc_regioni')
df = regioni_df.groupby('regione').nth(-1).reset_index()

In [2]:
def todays_bars(field, title='Nuovi positivi oggi'):
    return alt.Chart(df).mark_bar().encode(
        x=field,
        y=alt.Y('regione:N', sort='-x'),
    ).properties(
        height=600,
        width=800
    ).transform_filter(
            (datum.percentuale_positivi > 0)
    ).properties(title=title + ', ' + str(df.data.iloc[0])).interactive()

In [3]:
todays_bars('nuovi_positivi')

alt.Chart(...)

In [4]:
todays_bars('nuovi_deceduti', title='Nuovi deceduti oggi')

alt.Chart(...)

In [5]:
def rolling_avg_facets(field, title, tooltip=['data', 'nuovi_positivi_per_1M_pop', 'nuovi_deceduti_per_1M_pop'], limit=400):
    base = alt.Chart().transform_window(
        averaged=f'mean({field})',
        frame=[-4,3],
        groupby=['regione']
    ).encode(
        x='data:T',
        tooltip=tooltip
    ).properties(
        height=150,
        width=150,
    )

    c1 = base.mark_line().encode(
        y=alt.Y('averaged:Q', title=''),
    )

    c2 = base.mark_bar(opacity=0.1).encode(
        y=alt.Y(f'{field}:Q', title='', scale=alt.Scale(domain=(0, limit))),

    )

    return alt.layer(c1, c2, data=regioni_df).facet(facet='regione:N', columns=6).properties(
        title={
          "text": [title], 
          "subtitle": ["Dato mediato su 7 giorni"]
        }
    ).interactive()

In [6]:
rolling_avg_facets('nuovi_positivi_per_1M_pop', title="Nuovi positivi per 1M di abitanti per regione")

alt.FacetChart(...)

In [7]:
rolling_avg_facets('nuovi_deceduti_per_1M_pop', title="Nuovi deceduti per 1M di abitanti per regione", limit=50)

alt.FacetChart(...)

In [8]:
alt.Chart(regioni_df).mark_line().transform_window(
    nuovi_deceduti_avg='mean(nuovi_deceduti)',
    frame=[-5, 0],
    groupby=['regione']
).encode(
    x='data:T',
    y=alt.Y('nuovi_deceduti_avg:Q', title=''),
    facet=alt.Facet('regione:N', columns=6), 
    tooltip=['regione', 'data', 'totale_casi', 'deceduti', 'totale_casi_per_1M_pop', 'deceduti_per_1M_pop']
).properties(
    height=150,
    width=150,
    title={
      "text": ["Nuovi deceduti per regione"], 
      "subtitle": ["Dato mediato su 5 giorni"]
    }
).resolve_scale(y='independent').interactive()

alt.Chart(...)

In [9]:
alt.Chart(regioni_df).mark_line().transform_window(
    nuovi_positivi_avg='mean(nuovi_positivi)',
    frame=[0,5],
    groupby=['regione']
).encode(
    x='data:T',
    y=alt.Y('nuovi_positivi_avg:Q', title=''),
    facet=alt.Facet('regione:N', columns=6), 
    tooltip=['regione', 'data', 'totale_casi', 'deceduti', 'totale_casi_per_1M_pop', 'deceduti_per_1M_pop']
).properties(
    height=150,
    width=150,
    title={
      "text": ["Nuovi positivi per regione"], 
      "subtitle": ["Dato mediato su 6 giorni"]
    }
).resolve_scale(y='independent')

alt.Chart(...)

In [10]:
alt.Chart(regioni_df).mark_line().encode(
    x='data:T',
    y=alt.Y('letalita:Q', title=''),
    facet=alt.Facet('regione:N', columns=6), 
    tooltip=['regione', 'data', 'totale_casi', 'deceduti', 'totale_casi_per_1M_pop', 'deceduti_per_1M_pop']
).properties(
    height=150,
    width=150,
    title={
      "text": ["Letalità per regione"], 
      "subtitle": ["Dato mediato su 6 giorni"]
    }
)

alt.Chart(...)

In [11]:
pnp = regioni_df[regioni_df.data > '2020-04-18']

alt.Chart(pnp).mark_line().transform_window(
    avg='mean(percentuale_nuovi_positivi)',
    frame=[0, 3],
    groupby=['regione']
).encode(
    x='data:T',
    y=alt.Y('avg:Q', title='', scale=alt.Scale(domain=(0, 15))),
    facet=alt.Facet('regione:N', columns=6), 
    tooltip=['regione', 'data', 'totale_casi', 'deceduti', 'totale_casi_per_1M_pop', 'deceduti_per_1M_pop']
).properties(
    height=150,
    width=150,
    title={
      "text": ["Percentuale nuovi positivi per regione"], 
      "subtitle": ["Calcolato come il rapporto tra nuovi casi positivi su nuovi casi testati", "Dato mediato su 3 giorni"]
    }
).interactive()

alt.Chart(...)

In [19]:
alt.Chart(df).mark_bar().encode(
    x='totale_casi_per_1M_pop:Q',
    y=alt.Y('regione:N', sort='-x'),
).properties(
    height=600,
    width=800,
    title='Totale casi per 1M pop per regione'
) | alt.Chart(df).mark_bar().encode(
    x='deceduti_per_1M_pop:Q',
    y=alt.Y('regione:N', sort='-x'),
).properties(
    height=600,
    width=800,
    title='Totale deceduti per 1M pop per regione'
)

alt.HConcatChart(...)